In [1]:
import pandas as pd
import geopandas as gpd
import numpy as np
from matplotlib import pyplot as plt
# This will add the .hvplot() function to your DataFrame!
import hvplot.pandas
# Import holoviews too
import holoviews as hv

In [2]:
demo = gpd.read_file(r'../Data/census/DEMO.geojson')
rent = gpd.read_file(r'../Data/census/Rent_BG4326.geojson')
rtcc = gpd.read_file(r'../Data/RTCC4326.geojson')
totals = pd.read_csv(r'../Data/census/justtotals.csv')
mort = gpd.read_file(r'../Data/census/Mort_BG4326.geojson')

In [3]:
for col in mort.columns: 
    print(col)

MTFCC
OID
GEOID
STATE
COUNTY
TRACT
BLKGRP
BASENAME
NAME_x
LSADC
FUNCSTAT
AREALAND
AREAWATER
CENTLAT
CENTLON
INTPTLAT
INTPTLON
OBJECTID
NAME_y
mortgage_50.0_P_more
Total_mortgage
Total_no_mortgage
no_mortgage_50.0_P_more
Grand_Total
block group
P_no_mortgage
P_mortgage
P_mort_50_P
P_no_mort_50_P
geometry


In [57]:
totals[["GEOID"]] = totals[["GEOID"]].astype(str)

In [58]:
totals.dtypes

GEOID      object
Totals    float64
dtype: object

In [59]:
demo_total = demo.merge(totals, on='GEOID',)

In [111]:
demo_total["Hisp_P"] = (demo_total["Total_Hispanic"] / demo_total["Totals_y"]) * 100
demo_total["NonWhite_P"] = 100 - demo_total["W_P"] 

In [196]:
demo_total[["W_P", "NonWhite_P"]]

W_P  NonWhite_P
0     0.000000  100.000000
1     3.164557   96.835443
2     0.000000  100.000000
3     0.000000  100.000000
4    77.684564   22.315436
..         ...         ...
491   8.321678   91.678322
492  54.262145   45.737855
493  91.098748    8.901252
494  85.790173   14.209827
495  18.217666   81.782334

[496 rows x 2 columns]

In [197]:
len(demo_total["W_P"].isna())

496

In [200]:
demo_total[demo_total["W_P"].isna()]["W_P"]

111   NaN
226   NaN
375   NaN
401   NaN
468   NaN
Name: W_P, dtype: float64

In [20]:
rtcc["PD_Distric"].unique()

array(['', ' '], dtype=object)

In [19]:
rtccplot = rtcc.hvplot(width=900,
            height=600,
            #alpha=0.6,
            geo=True,
                      color="white",
                      line_color="black",
                      size=40)

In [20]:
rtccplot

:Points   [Longitude,Latitude]

In [205]:
demoplot = demo_total_final.hvplot(c="NonWhite_P",
            width=900,
            height=600,
            geo=True,
                                   alpha=0.6,
           cmap='plasma',
            hover_cols=['GEOID','M_Teens_P', 'Camera_Count'],
                            line_color="gray")

In [193]:
demoplot

:Polygons   [Longitude,Latitude]   (NonWhite_P,GEOID,M_Teens_P,Camera_Count)

In [203]:
demoplot

:Polygons   [Longitude,Latitude]   (NonWhite_P,GEOID,M_Teens_P,Camera_Count)

In [206]:
 demoplot  *rtccplot

:Overlay
   .Polygons.I :Polygons   [Longitude,Latitude]   (NonWhite_P,GEOID,M_Teens_P,Camera_Count)
   .Points.I   :Points   [Longitude,Latitude]

In [15]:
rentplot = rent_final.hvplot(c="P40P",
            width=900,
            height=600,
            geo=True,
                                   alpha=0.6,
           cmap='plasma',
            hover_cols=['Camera_Count'],
                            line_color="gray")

In [16]:
rentplot

:Polygons   [Longitude,Latitude]   (P40P,Camera_Count)

In [10]:
mortplot50 = mort_final.hvplot(c="P_mort_50_P",
            width=900,
            height=600,
            geo=True,
                                   alpha=0.6,
           cmap='plasma',
            hover_cols=['Camera_Count'],
                            line_color="gray")

In [11]:
mortplot50

:Polygons   [Longitude,Latitude]   (P_mort_50_P,Camera_Count)

In [21]:
mortplot50*rtccplot

:Overlay
   .Polygons.I :Polygons   [Longitude,Latitude]   (P_mort_50_P,Camera_Count)
   .Points.I   :Points   [Longitude,Latitude]

In [242]:
rentplot50 *rtccplot

:Overlay
   .Polygons.I :Polygons   [Longitude,Latitude]   (P50_moreP,Camera_Count)
   .Points.I   :Points   [Longitude,Latitude]

In [17]:
cameraplot = rent_final.hvplot(c="Camera_Count",
            width=900,
            height=600,
            geo=True,
                                   alpha=0.6,
           cmap='plasma',
            hover_cols=['GEOID','M_Teens_P', 'NonWhite_P'],
                            line_color="gray")

In [18]:
cameraplot

:Polygons   [Longitude,Latitude]   (Camera_Count,GEOID)

# Making Camera Counts

In [4]:
for col in mort.columns: 
    print(col)

MTFCC
OID
GEOID
STATE
COUNTY
TRACT
BLKGRP
BASENAME
NAME_x
LSADC
FUNCSTAT
AREALAND
AREAWATER
CENTLAT
CENTLON
INTPTLAT
INTPTLON
OBJECTID
NAME_y
mortgage_50.0_P_more
Total_mortgage
Total_no_mortgage
no_mortgage_50.0_P_more
Grand_Total
block group
P_no_mortgage
P_mortgage
P_mort_50_P
P_no_mort_50_P
geometry


## MortCamera

In [8]:
## Trying to do a St_contains, so that I have data in the mort gejson about how many cameras are in each blockgroup

## first just get GEOID, geometry from mort
mort_geo = mort[["GEOID", "geometry"]]


## Then get buffer around cameras, of like 500 ft
    ## first convert crs of both
mort_geo = mort_geo.to_crs(3452)
rtcc_3452 = rtcc.to_crs(3452)

    ## Then make Buffer
rtcc_3452["buffer"] = rtcc_3452.buffer(500)
rtccbuffer = rtcc_3452[["buffer"]]
rtccbuffer["Camera_Count"] = 1  ## for counts
    
    ## make rtcc back into a gpd
rtccbuffer = gpd.GeoDataFrame(rtccbuffer, geometry="buffer")
    
## Then st_intersects with rtcc, is still sjoin??
mort_rtcc = gpd.sjoin(mort_geo, rtccbuffer, how='left')

## then group by geoid and count 
mort_rtcc = mort_rtcc[["GEOID", "Camera_Count"]] 
mort_rtcc["Camera_Count"] = mort_rtcc["Camera_Count"].fillna(0)
mort_rtcc = mort_rtcc.groupby(by="GEOID", as_index=False).sum() 

## Then merge back to mort_total
mort_final = mort.merge(mort_rtcc, on="GEOID")

C:\Users\brine\AppData\Local\Temp/ipykernel_15532/1363527287.py:15: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  rtccbuffer["Camera_Count"] = 1  ## for counts


In [9]:
mort_final =mort_final.to_crs(4326)
mort_final.to_file("mortCamera_BG4326.geojson", driver='GeoJSON')

## DemoCamera

In [188]:
## Trying to do a St_contains, so that I have data in the demo gejson about how many cameras are in each blockgroup

## first just get GEOID, geometry from demo
demo_geo = demo[["GEOID", "geometry"]]


## Then get buffer around cameras, of like 500 ft
    ## first convert crs of both
demo_geo = demo_geo.to_crs(3452)
rtcc_3452 = rtcc.to_crs(3452)

    ## Then make Buffer
rtcc_3452["buffer"] = rtcc_3452.buffer(500)
rtccbuffer = rtcc_3452[["buffer"]]
rtccbuffer["Camera_Count"] = 1  ## for counts
    
    ## make rtcc back into a gpd
rtccbuffer = gpd.GeoDataFrame(rtccbuffer, geometry="buffer")
    
## Then st_intersects with rtcc, is still sjoin??
demo_rtcc = gpd.sjoin(demo_geo, rtccbuffer, how='left')

## then group by geoid and count 
demo_rtcc = demo_rtcc[["GEOID", "Camera_Count"]] 
demo_rtcc["Camera_Count"] = demo_rtcc["Camera_Count"].fillna(0)
demo_rtcc = demo_rtcc.groupby(by="GEOID", as_index=False).sum() 

## Then merge back to demo_total
demo_total_final = demo_total.merge(demo_rtcc, on="GEOID")

C:\Users\brine\AppData\Local\Temp/ipykernel_17324/3132355691.py:15: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  rtccbuffer["Camera_Count"] = 1  ## for counts


In [228]:
demo_total_final = demo_total_final.to_crs(4326)
demo_total_final.to_file("DemoCamera_BG4326.geojson", driver='GeoJSON')

## RentCamera

In [14]:
## Trying to do a St_contains, so that I have data in the demo gejson about how many cameras are in each blockgroup

## first just get GEOID, geometry from demo
rent_geo = demo[["GEOID", "geometry"]]


## Then get buffer around cameras, of like 500 ft
    ## first convert crs of both
rent_geo = rent_geo.to_crs(3452)
rtcc_3452 = rtcc.to_crs(3452)

    ## Then make Buffer
rtcc_3452["buffer"] = rtcc_3452.buffer(500)
rtccbuffer = rtcc_3452[["buffer"]]
rtccbuffer["Camera_Count"] = 1  ## for counts
    
    ## make rtcc back into a gpd
rtccbuffer = gpd.GeoDataFrame(rtccbuffer, geometry="buffer")
    
## Then st_intersects with rtcc, is still sjoin??
rent_rtcc = gpd.sjoin(rent_geo, rtccbuffer, how='left')

## then group by geoid and count 
rent_rtcc = rent_rtcc[["GEOID", "Camera_Count"]] 
rent_rtcc["Camera_Count"] = rent_rtcc["Camera_Count"].fillna(0)
rent_rtcc = rent_rtcc.groupby(by="GEOID", as_index=False).sum() 

## Then merge back to demo_total 
rent_final = rent.merge(rent_rtcc, on="GEOID")

C:\Users\brine\AppData\Local\Temp/ipykernel_15532/3735236872.py:15: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  rtccbuffer["Camera_Count"] = 1  ## for counts


In [221]:
rent_final = rent_final.fillna(0)

In [218]:

rent_final.head()

MTFCC              OID         GEOID STATE COUNTY   TRACT BLKGRP BASENAME  \
0  G5030    2085970206340  220710009024    22    071  000902      4        4   
1  G5030    2085970206231  220710009032    22    071  000903      2        2   
2  G5030    2085970206298  220710009033    22    071  000903      3        3   
3  G5030    2085970206506  220710009034    22    071  000903      4        4   
4  G5030  208593776264718  220710120002    22    071  012000      2        2   

          NAME_x LSADC  ... OBJECTID  \
0  Block Group 4    BG  ...     1198   
1  Block Group 2    BG  ...     1199   
2  Block Group 3    BG  ...     1200   
3  Block Group 4    BG  ...     1201   
4  Block Group 2    BG  ...      921   

                                              NAME_y  Totals adj_total  \
0  Block Group 4, Census Tract 9.02, Orleans Pari...    26.0      26.0   
1  Block Group 2, Census Tract 9.03, Orleans Pari...    35.0      24.0   
2  Block Group 3, Census Tract 9.03, Orleans Pari...    17.0      17.0   
3  Block Group 4, Census Tract 9.03, Orleans Pari...    37.0      21.0   
4  Block Group 2, Census Tract 120, Orleans Paris...    33.0      33.0   

   P50_moreP       P40P       P30P  block group  \
0  76.923077  23.076923   0.000000            4   
1  37.500000   0.000000   0.000000            2   
2  70.588235   0.000000   0.000000            3   
3  80.952381   0.000000  19.047619            4   
4  48.484848   0.000000   0.000000            2   

                                            geometry  Camera_Count  
0  POLYGON ((-90.01759 29.97367, -90.01724 29.974...           0.0  
1  POLYGON ((-90.01968 29.96748, -90.01934 29.968...           1.0  
2  POLYGON ((-90.01416 29.96956, -90.01382 29.970...           0.0  
3  POLYGON ((-90.01865 29.97058, -90.01830 29.971...           1.0  
4  POLYGON ((-90.13128 29.93452, -90.13086 29.935...           1.0  

[5 rows x 27 columns]

In [229]:
rent_final =rent_final.to_crs(4326)
rent_final.to_file("RentCamera_BG4326.geojson", driver='GeoJSON')

In [231]:
rent_final.crs

<Geographic 2D CRS: EPSG:4326>
Name: WGS 84
Axis Info [ellipsoidal]:
- Lat[north]: Geodetic latitude (degree)
- Lon[east]: Geodetic longitude (degree)
Area of Use:
- name: World.
- bounds: (-180.0, -90.0, 180.0, 90.0)
Datum: World Geodetic System 1984
- Ellipsoid: WGS 84
- Prime Meridian: Greenwich